# About tstree space

A *tstree* object created from the smarter dataset occupies a lot of space. Even 
by providing *REF* allele as ancestor alleles and dropping mutation in tstree object
there is still a lot of space occupied by the object. So try to deal with *tables* 
and inspect how much data is stored here

In [1]:
from pprint import pprint
import numpy as np

import tskit

from tskitetude import get_project_dir

In [2]:
ts = tskit.load(str(get_project_dir() / "results-reference/background_samples/tsinfer/SMARTER-OA-OAR3-forward-0.4.10.focal.26.trees"))
ts

Inspecting table nodes:

In [3]:
print(f"Nodes are {len(ts.tables.nodes)}")
pprint(ts.tables.nodes.asdict())
pprint(ts.tables.nodes[-1])

Nodes are 21910
{'flags': array([1, 1, 1, ..., 0, 0, 0], dtype=uint32),
 'individual': array([ 0,  0,  1, ..., -1, -1, -1], dtype=int32),
 'metadata': array([123,  34, 109, ...,  55,  52, 125], dtype=int8),
 'metadata_offset': array([     0,      0,      0, ..., 544244, 544295, 544346], dtype=uint64),
 'metadata_schema': '',
 'population': array([ 0,  0,  0, ..., -1, -1, -1], dtype=int32),
 'time': array([0.00000000e+00, 0.00000000e+00, 0.00000000e+00, ...,
       6.20341018e+01, 2.29696449e+01, 3.64013888e+04])}
NodeTableRow(flags=0, time=36401.38882373234, population=-1, individual=-1, metadata=b'{"mn": 36401.38882373234, "vr": 216075121.75475174}')


It seems that are *edges* the most predominant data structure in *tstree* object:

In [4]:
print(f"Edges are {len(ts.tables.edges)}")
pprint(ts.tables.edges.asdict())
pprint(ts.tables.edges[-1])

Edges are 2399964
{'child': array([    1,    27,    45, ..., 20326, 20328, 21240], dtype=int32),
 'left': array([ 2239615.,  2239615.,  4467736., ..., 44004281., 44004281.,
       44004281.]),
 'metadata': array([], dtype=int8),
 'metadata_offset': array([0, 0, 0, ..., 0, 0, 0], dtype=uint64),
 'metadata_schema': '',
 'parent': array([13272, 13272, 13272, ..., 21909, 21909, 21909], dtype=int32),
 'right': array([ 6478894.,  6478894.,  5550505., ..., 44004282., 44004282.,
       44004282.])}
EdgeTableRow(left=44004281.0, right=44004282.0, parent=21909, child=21240, metadata=b'')


Ok, try to focus only on a SNP. Get the tree for the first SNP and try to get stuff
from tables:

In [5]:
POS = 209049
tree = ts.at(POS)
tree

Now get the intervals of this tree. Then try to filter out edges between those positions:

In [6]:
interval = tree.interval
left_bound = interval.left
right_bound = interval.right

filtered_edges = ts.tables.edges[
    np.logical_and(ts.tables.edges.left >= left_bound, ts.tables.edges.right <= right_bound)]
filtered_edges[:10]

In [7]:
len(filtered_edges)

3779

Can I filter out the nodes in the same way? In this case I don't have a left and right 
position like in the edge table. However, from the edge table I can derive which nodes are
*child* of *parents*:

In [8]:
parents = set(filtered_edges.parent)
childs = set(filtered_edges.child)

node_ids = parents.union(childs)
print(f"Got {len(node_ids)} distinct nodes")


Got 3781 distinct nodes


In [9]:
tree.draw_svg(
    size=(800, 400),
    time_scale="log_time",
)